In [1]:
import gym
import matplotlib.pyplot as plt
import numpy as np

In [2]:
from torch import nn
import torch
import random 

In [3]:
from torchvision import transforms as T

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

In [ ]:
import urllib.request
urllib.request.urlretrieve('http://www.atarimania.com/roms/Roms.rar','Roms.rar')
!pip install unrar
!unrar x Roms.rar
!mkdir rars
!mv HC\ ROMS.zip   rars
!mv ROMS.zip  rars
!python -m atari_py.import_roms rars

Streaming output truncated to the last 5000 lines.
Extracting  ROMS/Air-Sea Battle - Air Sea Battle (Anti-Aircraft) (1977) (Atari, Larry Kaplan) (CX2602, CX2602P) (PAL).bin       1%  OK 
Extracting  ROMS/Air-Sea Battle - Air Sea Battle - Target Fun (Anti-Aircraft) (1977) (Atari, Larry Kaplan - Sears) (CX2602 - 99802, 6-99802, 49-75102) ~.bin       1%  OK 
Extracting  ROMS/Airlock (1982) (Data Age) (DA1004) (Prototype).bin        1%  OK 
Extracting  ROMS/Airlock (1982) (Data Age) (DA1004) ~.bin                  1%  OK 
Extracting  ROMS/Airlock (1983) (Gameworld) (133-004) (PAL).bin            1%  OK 
Extracting  ROMS/Alices Abenteuer - Lilly Adventure (1983) (Quelle - Otto Versand) (732.273 8 - 600273, 781644) (PAL).bin       1%  OK 
Extracting  ROMS/Alien (1982) (20th Century Fox Video Games, Douglas 'Dallas North' Neubauer) (11006) ~.bin       1%  OK 
Extracting  ROMS/Alien (CCE).bin                                        

In [ ]:
!python -m atari_py.import_roms ROMS

copying ms_pacman.bin from ROMS/Ms. Pac-Man (1983) (Atari - GCC, Mark Ackerman, Glenn Parker) (CX2675) ~.bin to /usr/local/lib/python3.7/dist-packages/atari_py/atari_roms/ms_pacman.bin
copying trondead.bin from ROMS/TRON - Deadly Discs (TRON Joystick) (1983) (M Network - INTV - APh Technological Consulting, Jeff Ronne, Brett Stutz) (MT5662) ~.bin to /usr/local/lib/python3.7/dist-packages/atari_py/atari_roms/trondead.bin
copying kangaroo.bin from ROMS/Kangaroo (1983) (Atari - GCC, Kevin Osborn) (CX2689) ~.bin to /usr/local/lib/python3.7/dist-packages/atari_py/atari_roms/kangaroo.bin
copying qbert.bin from ROMS/Q-bert (1987) (Atari) (CX26150).bin to /usr/local/lib/python3.7/dist-packages/atari_py/atari_roms/qbert.bin
copying freeway.bin from ROMS/Freeway (1981) (Activision, David Crane) (AG-009, AG-009-04) ~.bin to /usr/local/lib/python3.7/dist-packages/atari_py/atari_roms/freeway.bin
copying krull.bin from ROMS/Krull (1983) (Atari, Jerome Domurat, Dave Staugas) (CX2682) ~.bin to /usr/lo

In [ ]:
env = gym.make('PongNoFrameskip-v4')
env = gym.wrappers.AtariPreprocessing(env, noop_max=30, frame_skip=4,
                                      screen_size=84, terminal_on_life_loss=False, 
                                      grayscale_obs=True, grayscale_newaxis=False, 
                                      scale_obs=False)

In [ ]:
class DQN(nn.Module):
    def __init__(self):
        super(DQN, self).__init__()
        self.conv1 = nn.Conv2d(1, 16, kernel_size=5, stride=2)
        self.bn1 = nn.BatchNorm2d(16)
        self.conv2 = nn.Conv2d(16, 32, kernel_size=5, stride=2)
        self.bn2 = nn.BatchNorm2d(32)
        self.conv3 = nn.Conv2d(32, 32, kernel_size=5, stride=2)
        self.bn3 = nn.BatchNorm2d(32)
        self.head = nn.Linear(32, 6)
        self.act = torch.nn.ReLU()
        self.pooling = torch.nn.AvgPool2d(5)

    def forward(self, x):
        x = self.act(self.bn1(self.conv1(x)))
        x = self.act(self.bn2(self.conv2(x)))
        x = self.act(self.bn3(self.conv3(x)))
        x = self.pooling(x)[:, :, 0, 0]
        return self.head(x.view(x.size(0), -1))

In [ ]:
from collections import namedtuple, deque

Transition = namedtuple('Transition',
                        ('state', 'action', 'next_state', 'reward'))


class ReplayMemory(object):
    def __init__(self, capacity):
        self.memory = deque([],maxlen=capacity)

    def push(self, *args):
        """Save a transition"""
        self.memory.append(Transition(*args))

    def sample(self, batch_size):
        return random.sample(self.memory, batch_size)

    def __len__(self):
        return len(self.memory)

In [ ]:
from tqdm.notebook import tqdm

In [ ]:
class Agent:
    def __init__(self, device='cpu', eps=0.9):
        self.device = device

        self.model = DQN().to(device)
        self.optimizer = torch.optim.Adam(self.model.parameters())

        self.target_model = DQN().to(device)
        self.target_model.load_state_dict(self.model.state_dict())
        self.memory = ReplayMemory(100000)
        # self.transforms = T.Compose([T.ToTensor()])
        self.transforms = lambda x: x/256.
        self.eps = eps
        self.n_actions = 6
        self.batch_size = 128
        
        self.GAMMA = 0.999

    def select_action(self, state, step):
        GAMMA = 0.99
        EPS_START = 1
        EPS_END = 0.02
        EPS_DECAY = 1000000

        eps_threshold = EPS_END + (EPS_START - EPS_END) * \
            np.exp(-1. * step / EPS_DECAY)
        state = self.transforms(torch.tensor([[state]])).to(self.device)        
        if np.random.rand() < eps_threshold:
            return np.random.randint(self.n_actions)
        else:
            with torch.no_grad():
                best_action = self.model(
                    self.transforms(state)
                )[0].argmax()
            return best_action.item()

    def push_memory(self, state, action, next_state, reward):
        if_tensor = lambda x: torch.tensor([[x]]) if x is not None else None
        self.memory.push(torch.tensor([[state]]), torch.tensor([[action]]), if_tensor(next_state), reward)
    
    def update_target_model(self):
        self.target_model.load_state_dict(self.model.state_dict())    

    def optimize_model(self,):
        if len(self.memory) < self.batch_size:
            return
        transitions = self.memory.sample(self.batch_size)
        # Transpose the batch (see https://stackoverflow.com/a/19343/3343043 for
        # detailed explanation). This converts batch-array of Transitions
        # to Transition of batch-arrays.
        batch = Transition(*zip(*transitions))

        # Compute a mask of non-final states and concatenate the batch elements
        # (a final state would've been the one after which simulation ended)
        non_final_mask = torch.tensor(tuple(map(lambda s: s is not None,
                                            batch.next_state)),  dtype=torch.bool)
        non_final_next_states = torch.cat([s for s in batch.next_state
                                                    if s is not None])
        non_final_next_states = self.transforms(non_final_next_states).to(self.device)
        state_batch = self.transforms(torch.cat(batch.state)).to(self.device)
        action_batch = torch.cat(batch.action)
        reward_batch = torch.cat(batch.reward)

        # Compute Q(s_t, a) - the model computes Q(s_t), then we select the
        # columns of actions taken. These are the actions which would've been taken
        # for each batch state according to policy_net

        state_action_values = self.model(state_batch).gather(1, action_batch.to(self.device))

        # Compute V(s_{t+1}) for all next states.
        # Expected values of actions for non_final_next_states are computed based
        # on the "older" target_net; selecting their best reward with max(1)[0].
        # This is merged based on the mask, such that we'll have either the expected
        # state value or 0 in case the state was final.
        next_state_values = torch.zeros(self.batch_size, device=self.device)        
        next_state_values[non_final_mask] = self.target_model(non_final_next_states).max(1)[0].detach()
        # Compute the expected Q values
        expected_state_action_values = (next_state_values * self.GAMMA) + reward_batch

        # Compute Huber loss
        criterion = nn.MSELoss()
        loss = criterion(state_action_values, expected_state_action_values.unsqueeze(1))        

        # Optimize the model
        self.optimizer.zero_grad()
        loss.backward()
        for param in self.model.parameters():
            param.grad.data.clamp_(-1, 1)
        self.optimizer.step()

In [ ]:
# from google.colab import drive
# drive.mount('/content/drive')

In [ ]:
from plotly import express as px
from plotly import graph_objects as go


In [ ]:
# ds = episodes[-2]['states'][:]
# fig = px.imshow(np.stack(ds),
#                 animation_frame=0,
#                 # animation_frame=episodes[0]['actions'][:255],
#                 # labels=dict(animation_frame="slice"),
#                 labels=dict(animation_frame="slice"),
#                 color_continuous_scale='gray')
# fig.show()

In [ ]:
device = 'cuda'
agent = Agent(device=device)

In [ ]:
num_episodes = 2000
total_steps = 0
total_rewards = []
episodes = []
for i_episode in range(num_episodes):
    # Initialize the environment and state
    total_rewards.append(0)
    state = env.reset()    
    episodes.append({'states' : [], 'actions' : []})
    for step in tqdm(range(1500)):        
        action = agent.select_action(state, step)
        episodes[-1]['states'].append(state)
        episodes[-1]['actions'].append(action)
        
        next_state, reward, done, _ = env.step(action)
        total_rewards[-1] += reward
        reward = torch.tensor([reward], device=device)        

        # Move to the next state 
        if done:
            next_state = None

        agent.push_memory(
            state, action, next_state, reward
        )
        state = next_state
        # Perform one step of the optimization (on the policy network)
        agent.optimize_model()
        if done:
            break
        total_steps += 1

    print(total_rewards[-1])
    if i_episode % 1 == 0:
        agent.update_target_model()    
    
    if i_episode % 10 == 0:
        torch.save(
            agent.model.state_dict(),
            '/content/drive/MyDrive/RL/model.pkl'
        )
        torch.save(
            np.array(total_rewards),
            '/content/drive/MyDrive/RL/total_rewards.pkl'
        )
        
        

  0%|          | 0/1500 [00:00<?, ?it/s]

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:26: UserWarning: Creating a tensor from a list of numpy.ndarrays is extremely slow. Please consider converting the list to a single numpy.ndarray with numpy.array() before converting to a tensor. (Triggered internally at  ../torch/csrc/utils/tensor_new.cpp:210.)


-21.0


  0%|          | 0/1500 [00:00<?, ?it/s]

-20.0


...

  0%|          | 0/1500 [00:00<?, ?it/s]

-19.0


  0%|          | 0/1500 [00:00<?, ?it/s]

-20.0


  0%|          | 0/1500 [00:00<?, ?it/s]